# Record3D Point Cloud Visualization

This notebook visualizes combined point clouds from all cameras to check alignment.


In [2]:
%load_ext autoreload
%autoreload 2

In [1]:
!source /workspace/Home_Reconstruction/venv/bin/activate
!pip install --upgrade ipykernel
!/workspace/Home_Reconstruction/venv/bin/python -m ipykernel install --user --name=home_recon_venv --display-name "Python (home_recon_venv)"
!pip install opencv-python
!pip install scikit-image scikit-learn
!pip install ninja


[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip
Installed kernelspec home_recon_venv in /root/.local/share/jupyter/kernels/home_recon_venv

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip


In [3]:
%autoreload 2
import sys
print(sys.executable)

import OpenEXR
from pathlib import Path

PROJECT_ROOT = Path('/workspace/Home_Reconstruction')
sys.path.insert(0, str(PROJECT_ROOT))  # only the parent folder

import scene
from scene.objectgs_model import *
from scene.train import *
from scene.vis_tools.pc_viewer import *

import scene.data_loaders 
from scene.data_loaders.record3d_loader import *
from scene.data_loaders.generate_masks import *

import gsplat

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
%matplotlib inline

/workspace/Home_Reconstruction/venv/bin/python
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


## Load And View Scene

In [3]:
%autoreload 2
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"
os.environ['PYTHONIOENCODING'] = 'utf-8'
from scene.data_loaders.generate_masks import *
from huggingface_hub import login
#paste login command w token here

scene_dir = "/workspace/Home_Reconstruction/data_scenes/maria_bedroom"
text_prompts = ["chair","book", "guitar", "bed", "plant", "lamp", "wall", "dresser", "mirror", "shelf", "picture", "postcard", "container", "computer", "clothing"]
n=20

# masks_dir, class_mapping = segment_and_save_incremental(
#     text_prompts=text_prompts,
#     scene_path=scene_dir,
#     n=(n*4),
#     resume=True,
    
# )

In [4]:
# Step 3: Use the class via the module (no wildcard import)
scene_obj = Record3DScene(
    scene_path=scene_dir,
    use_semantics=True,
    subsample=4,
    frame_step=n,
    redo_semantics=False,
)

# Step 4: Check results
print(f"\nSemantic Point Cloud Summary:")
print(f"  Total points: {len(scene_obj.points):,}")
print(f"  Unique objects: {scene_obj.num_objects}")
print(f"  Object IDs: {scene_obj.get_object_ids_list()}")

Loaded metadata from /workspace/Home_Reconstruction/data_scenes/maria_bedroom/EXR_RGBD/metadata.json
  Image dimensions: 720x960
  Number of frames: 9720

Dataset split:
  Training: 486 frames
  Testing:  97 frames

Creating 486 cameras...


Loading cameras: 100%|██████████| 486/486 [00:16<00:00, 29.57it/s]


Created 486 cameras

Creating 97 cameras...


Loading cameras: 100%|██████████| 97/97 [00:04<00:00, 23.07it/s]


Created 97 cameras

Loading point cloud...
Loading semantic point cloud from /workspace/Home_Reconstruction/data_scenes/maria_bedroom/processed_semantic.ply
  Loaded 1,876,885 points with 61 unique objects

Semantic Point Cloud Summary:
  Total points: 1,876,885
  Unique objects: 61
  Object IDs: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60]


In [4]:
%autoreload 2
# Visualize with semantic colors and legend
visualize_pointclouds(
    scene_dir,
    ["processed_semantic.ply"],
    color_by_semantics=True,
    prompts=text_prompts,
)
# # Visualize with semantic colors and legend
# visualize_pointclouds(
#     scene_dir,
#     ["processed_semantic.ply"],
#     color_by_semantics=False,
#     prompts=text_prompts,
# )

✓ Loaded class mapping from class_mapping.json: 85 objects

Loading 1 point cloud(s) from maria_bedroom
🎨 Coloring by SEMANTIC OBJECT ID

Loading processed_semantic.ply...
  ✓ Loaded object IDs: 61 unique objects
      background: 1,392,063 points
      1: chair: 13,206 points
      2: chair: 99 points
      3: book: 1,102 points
      4: book: 1,199 points
      5: book: 595 points
      6: book: 94 points
      7: book: 3,963 points
      8: guitar: 1,108 points
      9: guitar: 25,147 points
      10: bed: 142 points
      11: bed: 257 points
      12: plant: 139 points
      13: plant: 3,530 points
      14: plant: 139,124 points
      15: lamp: 126,829 points
      16: lamp: 43,694 points
      17: wall: 20,719 points
      18: wall: 5,553 points
      19: wall: 2,572 points
      20: wall: 194 points
      21: wall: 584 points
      22: wall: 25,075 points
      23: wall: 3,025 points
      24: wall: 159 points
      25: dresser: 8,985 points
      26: mirror: 786 points
      27


Summary:
processed_semantic.ply          1,876,885 points (150,000 displayed)

🎨 Object Legend:
----------------------------------------
  background                (111,213 pts)
  1: chair                  (1,041 pts)
  2: chair                  (9 pts)
  3: book                   (88 pts)
  4: book                   (93 pts)
  5: book                   (55 pts)
  6: book                   (6 pts)
  7: book                   (305 pts)
  8: guitar                 (99 pts)
  9: guitar                 (1,981 pts)
  10: bed                   (13 pts)
  11: bed                   (26 pts)
  12: plant                 (16 pts)
  13: plant                 (290 pts)
  14: plant                 (11,173 pts)
  15: lamp                  (10,171 pts)
  16: lamp                  (3,456 pts)
  17: wall                  (1,645 pts)
  18: wall                  (434 pts)
  19: wall                  (218 pts)
  20: wall                  (15 pts)
  21: wall                  (60 pts)
  22: wall           

In [5]:
# TRAIN A MODEL FROM SCRATCH
import os
os.environ["PYTHONIOENCODING"] = "utf-8"

import torch
import importlib
import glob
from pathlib import Path

# Reload
import scene.train
import scene.objectgs_model
importlib.reload(scene.train)
importlib.reload(scene.objectgs_model)

from scene.train import GaussianTrainer
from scene.objectgs_model import ObjectGSModel

RESUME_FROM_CHECKPOINT = False
training_run_n = "training_run_2"

model = ObjectGSModel(
    point_cloud=scene_obj.points,
    colors=scene_obj.colors,
    object_ids=scene_obj.object_ids,
    object_names=text_prompts,
    voxel_size=0.02,
    k=10,
).to("cuda")

config = {
    # =================================================================
    # LEARNING RATES 
    # =================================================================
    "lr": 0.001,
    "lr_feature": 0.0025,
    "lr_position": 0.00016,
    "lr_scaling": 0.005,
    
    # =================================================================
    # TRAINING DURATION
    # =================================================================
    "num_iterations": 10000,
    "eval_interval": 1000,
    
    # =================================================================
    # PROGRESSIVE RESOLUTION
    # (shorter + more aggressive warmup)
    # =================================================================
    "use_progressive_resolution": True,
    "progressive_resolution_schedule": [
        (0.02, 4),    # was (0.01, 4)
        (0.08, 2),    # was (0.04, 2)
        (0.90, 1),    # was (0.95, 1)
    ],
    
    # =================================================================
    # LOSS WEIGHTS
    # (tighter scale control)
    # =================================================================
    "lambda_ssim": 0.3,
    "lambda_volume": 0.0001,
    "lambda_scale_reg": 3.0,   # was 1.0
    "max_scale": 0.05,         # was 0.1
    # NOTE: scale_threshold REMOVED (unused in trainer)
    
    # =================================================================
    # SEMANTIC LOSS
    # (delayed + warmed in)
    # =================================================================
    "use_semantic_loss": True,
    "lambda_semantic": 0.05,
    "semantic_loss_start": 4000,   # was 2000
    "semantic_warmup_iters": 1500, # was 0
    
    # =================================================================
    # DENSIFICATION
    # (earlier + more aggressive)
    # =================================================================
    "use_densification": True,
    "densify_start": 200,              # was 500
    "densify_until": 7000,             # was 8000
    "densify_interval": 250,           # was 500
    "densify_grad_threshold": 3e-5,    # was 5e-5
    "prune_opacity_threshold": 0.005,  # was 0.01
    # NOTE: min_opacity REMOVED (unused by trainer)
    
    # =================================================================
    # CHECKPOINTING
    # =================================================================
    "checkpoint_topk": 3,
    "checkpoint_metric": "test_l1",
    "lower_is_better": True,
    "progress_render_scale": 0.5,
    
    # =================================================================
    # EARLY STOPPING
    # =================================================================
    "early_stop_patience_evals": 20,
}


start_iteration = 0
latest_ckpt = None

if RESUME_FROM_CHECKPOINT:
    ckpt_dir = PROJECT_ROOT / "outputs" / "maria_bedroom" / training_run_n / "checkpoints"
    checkpoints = sorted(glob.glob(str(ckpt_dir / "*.pth")))

    if checkpoints:
        latest_ckpt = checkpoints[-1]
        print(f"Loading checkpoint: {latest_ckpt}")
        ckpt = torch.load(latest_ckpt, map_location="cuda")

        # Support both common formats
        if "model_state_dict" in ckpt:
            model.load_state_dict(ckpt["model_state_dict"])
            start_iteration = int(ckpt.get("iteration", 0))
        else:
            model.load_state_dict(ckpt)
            # infer from filename if needed
            stem = Path(latest_ckpt).stem  # checkpoint_010000
            try:
                start_iteration = int(stem.split("_")[-1])
            except Exception:
                start_iteration = 0

        print(f"Resumed from iteration {start_iteration}")
    else:
        print("No checkpoint found, starting fresh")

trainer = GaussianTrainer(
    model=model,
    scene=scene_obj,
    scene_name="maria_bedroom",
    config=config,
    base_output_dir=str(PROJECT_ROOT / "outputs"),
)

trainer.train()
#trainer.export_best_marble(latest_ckpt)


08:00:15 | INFO    | ======================================================================
08:00:15 | INFO    | LOG FILE: /workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_4/training_run_4.log
08:00:15 | INFO    | ======================================================================
08:00:15 | INFO    | Optimizer: Adam with 4 param groups
08:00:15 | INFO    |   features: lr=0.002500 (18961696 params)
08:00:15 | INFO    |   scalings: lr=0.005000 (592553 params)
08:00:15 | INFO    |   offsets: lr=0.000160 (17776590 params)
08:00:15 | INFO    |   mlp: lr=0.001000 (45358 params)
08:00:15 | INFO    | INITIALIZING GaussianTrainer
08:00:15 | INFO    | ----------------------------------------------------------------------
08:00:15 | INFO    | Device: cuda
08:00:15 | INFO    | Train cams: 486 | Test cams: 97
08:00:15 | INFO    | Iterations: 10000
08:00:15 | INFO    | Progressive schedule (end_iter, downscale): [(200, 4), (1000, 2), (10000, 1)]
08:00:15 | INFO    | ------------

{'marble_scene_ply': PosixPath('/workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_4/final_outputs/splats_marble_010000.ply'),
 'marble_objects_dir': PosixPath('/workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_4/final_outputs/marble_objects'),
 'history': PosixPath('/workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_4/final_outputs/training_history.json')}

In [ ]:
from time_training import profile

# After creating trainer
profile(trainer, num_iterations=100)

In [14]:
import torch
import gc

# # Delete your objects
# if trainer:
#     del trainer

# if model:
# #     del model
# del trainer
# del model

# Clear Python garbage
gc.collect()

# Clear CUDA cache
torch.cuda.empty_cache()

# Verify
print(f"Allocated: {torch.cuda.memory_allocated() / 1e9:.2f} GB")
print(f"Reserved: {torch.cuda.memory_reserved() / 1e9:.2f} GB")

print(torch.cuda.memory_summary(device='cuda:0', abbreviated=False))

import gc
import torch

tensors = []
for obj in gc.get_objects():
    try:
        if torch.is_tensor(obj) and obj.is_cuda:
            size_mb = obj.element_size() * obj.numel() / 1e6
            tensors.append((size_mb, obj.shape, obj.dtype))
    except:
        pass

print(f"Found {len(tensors)} CUDA tensors")
print(f"Total: {sum(t[0] for t in tensors):.1f} MB")
print()
print("Top 20 largest:")
print("-" * 70)
for size_mb, shape, dtype in tensors[:20]:
    print(f"{size_mb:>10.2f} MB  {str(shape):40s} {dtype}")


Allocated: 7.00 GB
Reserved: 7.22 GB
|===========================================================================|
|                  PyTorch CUDA memory summary, device ID 0                 |
|---------------------------------------------------------------------------|
|            CUDA OOMs: 0            |        cudaMalloc retries: 0         |
|===========================================================================|
|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |
|---------------------------------------------------------------------------|
| Allocated memory      |   6676 MiB |  14173 MiB | 367360 GiB | 367354 GiB |
|       from large pool |   6393 MiB |  13888 MiB | 365818 GiB | 365812 GiB |
|       from small pool |    283 MiB |    302 MiB |   1542 GiB |   1541 GiB |
|---------------------------------------------------------------------------|
| Active memory         |   6676 MiB |  14173 MiB | 367360 GiB | 367354 GiB |
|       from large pool |  

In [13]:
from pathlib import Path

# ============================================================
# View individual object PLYs from training output
# ============================================================

# # Point to your training run's objects folder
# run_dir = Path("/workspace/Home_Reconstruction/outputs/maria bedroom/training_run_7/final_outputs/objects")

# # List available objects
# print("Available objects:")
# for ply in sorted(run_dir.glob("*.ply")):
#     print(f"  {ply.name}")

# # View a single object by ID
# object_id = 8  # e.g., 1 = nightstand
# ply_file = list(run_dir.glob(f"{object_id:02d}_*.ply"))[0]
# visualize_pointclouds(run_dir, [ply_file.name])



# Point to your training run's objects folder
splat_dir = Path("/workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_3/final_outputs")
ply_name = "splat_supersplat.ply"
visualize_pointclouds(splat_dir, [ply_name])

SyntaxError: invalid syntax (1280567074.py, line 24)

In [ ]:
# ============================================================
# Run the pipeline
# ============================================================
# Comprehensive bedroom prompts
text_prompts = [
    # Main furniture
    "bed",
    "nightstand",
    "dresser",
    "desk",
    "chair",
    "wardrobe",
    "mirror",
    "clothing",
    "jacket",
    "shirt",
    
    # Lighting
    "lamp",
    "ceiling light",
    
    # Textiles
    "pillow",
    "blanket",
    "curtain",
    "rug",
    
    # Structure
    "wall",
    "floor",
    "ceiling",
    "door",
    "window",
    
    # Decor
    "plant",
    "picture frame",
    "book",
    "jewelry",
    "monitor",
    "laptop",
    "jacket",
    "towel",
    "paper",
    "computer",
    "shelf",
    "poster",
    "postcard",
]